In [16]:
import pandas as pd
import tqdm
import numpy as np
from tqdm import tqdm
import json
import csv
import random
import ast

In [94]:
def remove_unnamed_column(df):
    df = df.loc[:, ~df.columns.str.contains('^Unnamed')]
    return df

def checknan(value):
    try:
        np.isnan(value) ==True
        return True
    except:
        return False
    
def get_data_not_null_of_column(df,column=None):
    df = df[df[column].notnull()]
    return df

In [95]:
df_raw_post = pd.read_csv('/home/phuongdx/python/GAPO/data/tbl_post_14_06_2021_raw.csv')
df_post = remove_unnamed_column(df = df_raw_post)
df_post = df_post.drop(['labeler', 'update_time'], axis = 1)
df_post.head(10)

id                                            content  \
0  qqv8vwce7dx1  Thân em như tấm lụa đào\nLụa này hơi đắt \nAnh...   
1  qqvr0i7zhqk3  The Remix đang sản xuất mùa tiếp theo, đ...   
2  qqvtcmhsghi6                                                NaN   
3  qqvteeqzjgvf  "Từng yêu nhau, từng là của nhau thật lâu\nĐến...   
4  qqvto67xm19w  📣THÊM 14 CA MẮC MỚI COVID-19 NHẬP CẢNH ĐÃ ĐƯỢC...   
5    qqvtp35pky               Chẳng biết cưa chàng bắt đầu từ đâu!   
6  qqvtschxj76i  Thả thính sáng giờ mà hổng dính anh nào hết 💖💖...   
7  qqvttshp0c61  Hôm nay là cá tháng tư, yêu em thì nói, dối lò...   
8  qqvtugl5260y            A là ai từ đâu bước đến nơi đây.\n..\n.   
9  qqvu224irk7f  Mứt dừa đi với chè xanh\nCòn e cũng phải có a ...   

                                               media  \
0  [{"height":1690,"image_id":"f1ff2054-b3d0-4e1e...   
1  [{"id":"f6782bfb-7327-415e-bd79-d907b611df3d",...   
2  [{"height":1932,"src":"https:\/\/gapo-image.st...   
3  [{"quality":"default","source":"source","categ...   
4  [{"id":"6b579079-271e-47c2-b662-0d40a1f42c5c",...   
5  [{"width":1152,"height":1647,"id":"57866b3b-2a...   
6  [{"id":"30f5def9-67ee-48ef-98ba-64a10d8f120b",...   
7  [{"type":"image","url":{"src":"\/images\/0a121...   
8  [{"height":960,"image_id":"52260e5f-26e5-4994-...   
9  [{"height":2048,"id":"13381927-e4ea-48e0-8f94-...   

                                               label  
0  [{"category":"giao-luu-ket-ban","labels":["nu-...  
1   [{"category":"showbiz-2","labels":["viet-nam"]}]  
2  [{"category":"giao-luu-ket-ban","labels":["nu-...  
3  [{"category":"giao-luu-ket-ban","labels":["nu-...  
4       [{"category":"tin-tuc-2","labels":["y-te"]}]  
5  [{"category":"giao-luu-ket-ban","labels":["nu-...  
6  [{"category":"giao-luu-ket-ban","labels":["nu-...  
7  [{"category":"giao-luu-ket-ban","labels":["nu-...  
8  [{"category":"giao-luu-ket-ban","labels":["nu-...  
9  [{"category":"giao-luu-ket-ban","labels":["nu-...

In [96]:
df_post.shape

(41230, 4)

In [97]:
temps_infos = []

num_of_error_media = 0
num_of_error_label = 0

for index, data in tqdm(df_post.iterrows()):
    post_id = data['id']
    content = data["content"]

#     if checknan(content) is True:
#         user_hashtag = np.nan
#         content_length = 0
#     else:
#         total_tags = []
#         content = content.replace("\n", " ")
#         content = content.replace("\r", " ")
# #         content_length = len(content)
#         tags     = content.split(" ")
#         tags_    = [tag.strip() for tag in tags if tag.startswith("#")]
#         for t in tags_:
#             total_tags += [i.lower() for i in t.split("#")[1:] if len(i)>1]
# #         if len(total_tags) == 0:
# #             user_hashtag = np.nan
#         else:
#             user_hashtag = '#'+ '#'.join(list(set(total_tags)))
    
    media = data["media"]
    label = data["label"]
    
    if checknan(media) is False:
        try:
            media_dict  = ast.literal_eval(media)
        except:
            media_dict  = json.loads(media)
    else:
        media_dict = []
    
    
    if checknan(label) is False:
        try:
            label_dict  = ast.literal_eval(label)
        except:
            label_dict  = json.loads(label)
    else:
        label_dict = []
        
        
    if len(label_dict)==0:
        num_of_error_label +=1
        gapo_hashtag = np.nan
    else:
        gapo_hashtag = "#" + "#".join([l['category'] for l in label_dict])
        print('******************')
        print(post_id)
        print(gapo_hashtag)
        print(label_dict)
        _gapo_hashtag = []
        try:
            _gapo_hashtag_ =  [ _gapo_hashtag +l['labels'] for l in label_dict]
        except:
            continue
        for l in label_dict:
            _gapo_hashtag += l['labels']

        gapo_hashtag = "#" + "#".join(_gapo_hashtag)
        
        
    if len(media_dict)==0 :
        num_of_error_media +=1
        image_src = np.nan
        image_id = np.nan
        continue
        
    
    for element in media_dict:
        if element["type"] !="image":
            image_src = np.nan
            image_id = np.nan
            continue
        else:
            image_src      = element["src"]
            image_id = image_src.split('/')[-1].split('.')[0]
        
        value = (post_id,image_id,content,image_src,gapo_hashtag)
        temps_infos.append(value)
        

columns = ["post_id","image_id","content","image_src","gapo_hashtag"]
df_gapo_cleaned = pd.DataFrame(temps_infos,columns=columns)

468it [00:00, 2294.60it/s]

******************
qqv8vwce7dx1
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvr0i7zhqk3
#showbiz-2
[{'category': 'showbiz-2', 'labels': ['viet-nam']}]
******************
qqvtcmhsghi6
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvteeqzjgvf
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvto67xm19w
#tin-tuc-2
[{'category': 'tin-tuc-2', 'labels': ['y-te']}]
******************
qqvtp35pky
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvtschxj76i
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu', 'tha-thinh']}]
******************
qqvttshp0c61
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvtugl5260y
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqvu224irk7f
#giao-luu-ket-ban
[{'category

698it [00:00, 2041.07it/s]

******************
qqx42q9c3fci
#tam-su
[{'category': 'tam-su', 'labels': ['tinh-yeu-hen-ho']}]
******************
qqx46yx31fye
#thu-cung#the-thao#home#xe-co#am-nhac
[{'category': 'thu-cung', 'labels': ['khac']}, {'category': 'the-thao', 'labels': ['khac']}, {'category': 'home', 'labels': ['khac']}, {'category': 'xe-co', 'labels': ['khac']}, {'category': 'am-nhac', 'labels': ['khac']}]
******************
qqx4dfs2mbwy
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
******************
qqx4e1x31fyg
#thu-cung
[{'category': 'thu-cung', 'labels': ['meo']}]
******************
qqx4yj52w
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['thoi-su']}]
******************
qqx4z4f0ecyw
#funny-2
[{'category': 'funny-2', 'labels': ['anh-che-hai-huoc']}]
******************
qqx5c6aljj23
#nghe-nghiep
[{'category': 'nghe-nghiep', 'labels': ['chia-se-kinh-nghiem']}]
******************
qqx5ep8t7ky
#giao-luu-ket-ban
[{'category': 'giao-luu-ket-ban', 'labels': ['nu-tu']}]
****************

1265it [00:00, 2457.42it/s]

...


qukiwjl8pbh
#tam-su
[{'category': 'tam-su', 'labels': ['tinh-yeu-hen-ho']}]
******************
qukixhl8pbh
#thu-choi
[{'category': 'thu-choi', 'labels': ['tho']}]
******************
qukixix31j3i
#funny
[{'category': 'funny', 'labels': ['anh-che-hai-huoc']}]
******************
qukj0h6sml
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['thoi-su']}]
******************
qukj2fl8pbh
#tam-su#thu-choi
[{'category': 'tam-su', 'labels': ['cuoc-song']}, {'category': 'thu-choi', 'labels': ['tho']}]
******************
qukj3t6sml
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['thoi-su']}]
******************
qukj4rl8pbh
#thu-choi
[{'category': 'thu-choi', 'labels': ['tho']}]
******************
qukj766sml
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['thoi-su']}]
******************
qukj778h58sp
#thu-choi#tam-su
[{'category': 'thu-choi', 'labels': ['tho']}, {'category': 'tam-su', 'labels': ['tinh-yeu-hen-ho']}]
******************
qukj8q6sml
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['thoi-su']}]
*********

40657it [00:14, 3000.22it/s]


quma3ox31fzc
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['khoa-hoc-cong-nghe']}]
******************
quma4qx31kxi
#du-lich
[{'category': 'du-lich', 'labels': ['dia-danh-du-lich']}]
******************
quma4zx31fza
#tin-tuc
[{'category': 'tin-tuc', 'labels': ['khoa-hoc-cong-nghe']}]
******************
quma5dale5h3
#tam-su
[{'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
quma5v52w
#the-thao-2
[{'category': 'the-thao-2', 'labels': ['bong-da']}]
******************
quma70npeaje
#tam-su
[{'category': 'tam-su', 'labels': ['tinh-yeu-hen-ho']}]
******************
quma95x31kxm
#du-lich#tam-su
[{'category': 'du-lich', 'labels': ['dia-danh-du-lich']}, {'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
qukmwyyd6r9
#khac
[{'category': 'khac', 'labels': ['lich-su']}]
******************
qumakppibt5c
#tam-su
[{'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
qumanab4wl5k
#tam-su
[{'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
q

41230it [00:14, 2895.43it/s]


quo3ed1mnhci
#tam-su
[{'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
quo3h1l74hud
#giao-duc
[{'category': 'giao-duc', 'labels': ['kien-thuc']}]
******************
quo3l9j0ypqt
#the-thao-2
[{'category': 'the-thao-2', 'labels': ['bong-da']}]
******************
quo3o0x31fy9
#am-thuc
[{'category': 'am-thuc', 'labels': ['review-an-uong']}]
******************
quo3olnu
#am-thuc
[{'category': 'am-thuc', 'labels': ['review-an-uong']}]
******************
quo3pg1mnhci
#tam-su
[{'category': 'tam-su', 'labels': ['cuoc-song']}]
******************
quo3t6h1uq46
#tam-su#am-nhac
[{'category': 'tam-su', 'labels': ['tinh-yeu-hen-ho']}, {'category': 'am-nhac', 'labels': ['pop-ballad']}]
******************
quo3tvrsdngx
#funny
[{'category': 'funny', 'labels': ['anh-che-hai-huoc']}]
******************
quo3x8x31kvr
#du-lich
[{'category': 'du-lich', 'labels': ['dia-danh-du-lich']}]
******************
quo41s1mnhci
#giao-duc
[{'category': 'giao-duc', 'labels': ['kien-thuc']}]
***************

In [98]:
df_gapo_cleaned.shape

(57185, 5)

In [99]:
df_gapo_cleaned_not_dup = df_gapo_cleaned.drop_duplicates(subset='post_id', keep='first').reset_index(drop=True)
df_gapo_cleaned_not_dup = get_data_not_null_of_column(df_gapo_cleaned_not_dup, column='gapo_hashtag')
df_gapo_cleaned_not_dup.shape

(35834, 5)

In [100]:
df_gapo_cleaned_not_dup.head(10)

post_id                              image_id  \
0  qqv8vwce7dx1  f1ff2054-b3d0-4e1e-a81e-14bcfcb98284   
1  qqvr0i7zhqk3  f6782bfb-7327-415e-bd79-d907b611df3d   
2  qqvtcmhsghi6  1a7e6c95-1f91-41e8-9d5b-269b0dbce86f   
3  qqvteeqzjgvf  58ac3938-d32e-4fe9-9e29-4a3a71e0e89a   
4  qqvto67xm19w  6b579079-271e-47c2-b662-0d40a1f42c5c   
5    qqvtp35pky  57866b3b-2a7d-4ae1-90e1-40185654140d   
6  qqvtschxj76i  30f5def9-67ee-48ef-98ba-64a10d8f120b   
7  qqvttshp0c61  0a1214bd-3d0e-43d9-9039-e41b3c891565   
8  qqvtugl5260y  52260e5f-26e5-4994-864d-f105b04a4996   
9  qqvu224irk7f  13381927-e4ea-48e0-8f94-2c49e3408b2c   

                                             content  \
0  Thân em như tấm lụa đào\nLụa này hơi đắt \nAnh...   
1  The Remix đang sản xuất mùa tiếp theo, đ...   
2                                                NaN   
3  "Từng yêu nhau, từng là của nhau thật lâu\nĐến...   
4  📣THÊM 14 CA MẮC MỚI COVID-19 NHẬP CẢNH ĐÃ ĐƯỢC...   
5               Chẳng biết cưa chàng bắt đầu từ đâu!   
6  Thả thính sáng giờ mà hổng dính anh nào hết 💖💖...   
7  Hôm nay là cá tháng tư, yêu em thì nói, dối lò...   
8            A là ai từ đâu bước đến nơi đây.\n..\n.   
9  Mứt dừa đi với chè xanh\nCòn e cũng phải có a ...   

                                           image_src      gapo_hashtag  
0  https://gapo-image.statics.pancake.vn/images/f...            #nu-tu  
1  https://gapo-image.statics.pancake.vn/images/f...         #viet-nam  
2  https://gapo-image.statics.pancake.vn/images/1...            #nu-tu  
3  https://gapo-image.statics.pancake.vn/images/5...            #nu-tu  
4  https://gapo-image.statics.pancake.vn/images/6...             #y-te  
5  https://gapo-image.statics.pancake.vn/images/5...            #nu-tu  
6  https://gapo-image.statics.pancake.vn/images/3...  #nu-tu#tha-thinh  
7  https://gapo-image.statics.pancake.vn/images/0...            #nu-tu  
8  https://gapo-image.statics.pancake.vn/images/5...            #nu-tu  
9  https://gapo-image.statics.pancake.vn/images/1...            #nu-tu

In [101]:
print(len(df_gapo_cleaned_not_dup))
label = df_gapo_cleaned_not_dup['gapo_hashtag']
# label[6]
# a = label[6].split('#')[1:]
labels = []
# print(label)
# print(label(1))
# for i in range(len(df_gapo_cleaned_not_dup)):
# #     print(label[i])
#     a = label[i].split('#')[1:]
#     labels.append(a)
#     print(label[i])
# print(type(label[1]))
# labels
for index, row in df_gapo_cleaned_not_dup.iterrows():
#     print(row['gapo_hashtag'])
    a = row['gapo_hashtag'].split('#')[1:]
    labels += a
labels
#     print(type(a))

35834


['nu-tu',
 'viet-nam',
 'nu-tu',
 'nu-tu',
 'y-te',
 'nu-tu',
 'nu-tu',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nam-thanh',
 'nu-tu',
 'nu-tu',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'cuoc-song',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'tinh-yeu-hen-ho',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nam-thanh',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'dan-ba',
 'nu-tu',
 'tinh-yeu-hen-ho',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'cuoc-song',
 'anh-che-hai-huoc',
 'nam-thanh',
 'tha-thinh',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nu-tu',
 'nam-thanh',
 'nu-tu',
 'nu-tu',
 'tinh-y

In [102]:
from collections import Counter
print(Counter(labels))

Counter({'nu-tu': 14250, 'tinh-yeu-hen-ho': 2990, 'cuoc-song': 2606, 'anh-che-hai-huoc': 1957, 'nam-thanh': 1858, 'lam-quen-ket-ban': 1796, 'bong-da': 1252, 'thoi-su': 1150, 'viet-nam': 1084, 'bien': 956, 'dia-danh-du-lich': 864, 'review-an-uong': 791, 'y-te': 731, 'o-to': 532, 'tha-thinh': 509, 'cong-thuc-nau-an-pha-che': 368, 'han-quoc': 364, 'ban-hang_ban-hang': 298, 'meo': 283, 'us-uk': 259, 'chup-anh-nghe-thuat': 242, 'xe-may': 232, 'checkin': 222, 'cho': 218, 'dien-thoai': 199, 'khoa-hoc-cong-nghe': 196, 'giai-tri': 196, 'gia-dinh_tre-con': 191, 'kien-thuc': 189, 'check-in': 176, 'cong-viec': 139, 'meme': 132, 'lich-su': 128, 'truyen-cam-hung': 124, 'tho': 123, 'chau-a': 116, 'tennis': 115, 'dinh-duong': 108, 'phong-canh': 107, 'ga': 101, 'hoi-hoa': 96, 'chia-se-kinh-nghiem': 96, 'khac': 91, 'giao-thong': 89, 'truyen-cuoi': 75, 'tablet-laptop-may-tinh': 70, 'game-chien-thuat-lol-dota-': 68, 'quan-ao': 66, 'sach': 66, 'dan-ba': 64, 'cham-soc': 62, 'tam-ly-tinh-cam': 60, 'piority-p

In [116]:
d = Counter(labels)
df = pd.DataFrame.from_dict(d, orient='index').reset_index()
df = df.rename(columns={'index':'label', 0:'count'})
df


label  count
0         nu-tu  14250
1      viet-nam   1084
2          y-te    731
3     tha-thinh    509
4     nam-thanh   1858
..          ...    ...
132    tai-lieu      2
133        phim      1
134  lofi-indie      1
135    cau-long      1
136      du-hoc      1

[137 rows x 2 columns]

In [192]:
df = df.loc[df['count'] >= 10]
df.shape

(100, 2)

In [121]:
bad_labels = ['phu-kien', 'tin-tuc', 'khac_cong-nghe-quan-su', 'trinh-tham-toi-pham', 'le-hoi-su-kien',
              'vo-thuat', 'graffiti', 'toc', 'khach-san-khu-nghi-duong', 'hai', 'yoga', 'pop-ballad', 
              'choi-ca-canh', 'khac_khoa-hoc-thien-van', 'game-bong-da', 'bieu-dien', 'truyen-hinh-thuc-te',
              'funny', 'dieu-khac', 'camera', 'game-giai-do', 'tai-lieu', 'dua-xe', 'cover', 'game-de-che',
              'smarthome', 'giay', 'danh-co', 'the-thao-am-nhac-drama', 'chien-tranh', 'suu-tam', 'do-an',
              'me-va-be', 'phim', 'lofi-indie', 'cau-long', 'du-hoc']

In [196]:
gapo_hashtags = []
c = 0
for index,data in tqdm(df_gapo_cleaned_not_dup.iterrows(),total=df_gapo_cleaned_not_dup.shape[0]):
    gapo_hashtag = data['gapo_hashtag']
    
    if not checknan(gapo_hashtag):
        gapo_hashtag = gapo_hashtag.split('#')[1:]

        gapo_hashtag = [f for f in gapo_hashtag if f in bad_labels]

#         print(gapo_hashtag)
        if len(gapo_hashtag) != 0: #Multi tag
#         if len(gapo_hashtag) == 1:
            gapo_hashtag = '2'
            c += 1
        else:
            gapo_hashtag = '1'
    gapo_hashtags.append(gapo_hashtag)
print('Count ', c)
    #print(gapo_hashtags)

100%|██████████| 35834/35834 [00:02<00:00, 14876.16it/s]

Count  99


In [205]:
# df_gapo_cleaned_not_dup.insert(loc=4, column='top_gapo_hashtag', value=gapo_hashtags)
d1 = df_gapo_cleaned_not_dup.loc[df_gapo_cleaned_not_dup['top_gapo_hashtag'] == '1']
# df_gapo_cleaned_not_dup.drop('top_gapo_hashtag', axis = 1, inplace = True)
# df_gapo_cleaned_not_dup.reset_index()
# df_gapo_cleaned_not_dup

In [206]:
d1

post_id                              image_id  \
0      qqv8vwce7dx1  f1ff2054-b3d0-4e1e-a81e-14bcfcb98284   
1      qqvr0i7zhqk3  f6782bfb-7327-415e-bd79-d907b611df3d   
2      qqvtcmhsghi6  1a7e6c95-1f91-41e8-9d5b-269b0dbce86f   
3      qqvteeqzjgvf  58ac3938-d32e-4fe9-9e29-4a3a71e0e89a   
4      qqvto67xm19w  6b579079-271e-47c2-b662-0d40a1f42c5c   
...             ...                                   ...   
36213  quoqzjhp0c61  4a029e19-68e8-40a3-b68a-9b3d2340d552   
36214  quor11sk0bl1  765e2df5-84b0-449e-84be-7874db188094   
36215  quor63x31fy9  58eca04d-6da3-4bf9-9787-c9158c38f10f   
36216  quor6ehr16kb  e71f1ae7-1c69-4eba-b5b1-25ef3f789dda   
36217  quor7mg4wbiz  bd67f266-e618-430e-a8e8-57c222226358   

                                                 content  \
0      Thân em như tấm lụa đào\nLụa này hơi đắt \nAnh...   
1      The Remix đang sản xuất mùa tiếp theo, đ...   
2                                                    NaN   
3      "Từng yêu nhau, từng là của nhau thật lâu\nĐến...   
4      📣THÊM 14 CA MẮC MỚI COVID-19 NHẬP CẢNH ĐÃ ĐƯỢC...   
...                                                  ...   
36213  Virus thì em âm tính \nNhưng thích anh thì em ...   
36214           Có khi nào anh thương em dù chỉ 1 lần ..   
36215  🥛 Sữa tươi trân châu THỐT NỐT miền Tây\n\nMới ...   
36216  Lí do em thấy nặng đầu \nTrên đầu có tóc trong...   
36217  Hoa rơi hoa rụng trước thèm \nEm đây còn ế lấy...   

                                               image_src top_gapo_hashtag  \
0      https://gapo-image.statics.pancake.vn/images/f...                1   
1      https://gapo-image.statics.pancake.vn/images/f...                1   
2      https://gapo-image.statics.pancake.vn/images/1...                1   
3      https://gapo-image.statics.pancake.vn/images/5...                1   
4      https://gapo-image.statics.pancake.vn/images/6...                1   
...                                                  ...              ...   
36213  https://gapo-image.statics.pancake.vn/images/4...                1   
36214  https://gapo-image.statics.pancake.vn/images/7...                1   
36215  https://gapo-image.statics.pancake.vn/images/5...                1   
36216  https://gapo-image.statics.pancake.vn/images/e...                1   
36217  https://image-5.gapo.vn/images/bd67f266-e618-4...                1   

          gapo_hashtag  
0               #nu-tu  
1            #viet-nam  
2               #nu-tu  
3               #nu-tu  
4                #y-te  
...                ...  
36213           #nu-tu  
36214           #nu-tu  
36215  #review-an-uong  
36216           #nu-tu  
36217           #nu-tu  

[35735 rows x 6 columns]

In [212]:
# d1.reset_index()
# d1.drop('top_gapo_hashtag', axis = 1, inplace = True)
# d1 = d1.reset_index()
d1.to_csv('/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_short_not_nan.csv')
# d1.drop(['index'], axis = 1, inplace = True)
# d1

In [125]:
top_labels = ['nu-tu', 'dia-danh-du-lich', 'viet-nam', 'tinh-yeu-hen-ho',
       'lam-quen-ket-ban', 'bien', 'funny', 'tha-thinh', 'ban-hang_ban-hang', 'bong-da', 'nam-thanh', 
       'anh-che-hai-huoc', 'cuoc-song', 'review-an-uong', 'meo', 'thoi-su', 'cho', 'dinh-duong',
       'do-uong', 'o-to', 'tin-tuc', 'us-uk', 'check-in', 'chau-a', 'y-te', 'checkin',
       'han-quoc', 'ga', 'xe-may', 'giao-thong', 'phong-canh']

In [127]:
gapo_hashtags = []

for index,data in tqdm(df_gapo_cleaned_not_dup.iterrows(),total=df_gapo_cleaned_not_dup.shape[0]):
    gapo_hashtag = data['gapo_hashtag']
    
    if not checknan(gapo_hashtag):
        gapo_hashtag = gapo_hashtag.split('#')[1:]
        
        gapo_hashtag = [f for f in gapo_hashtag if f in top_labels]
        print(gapo_hashtag)
        if len(gapo_hashtag) != 0: #Multi tag
#         if len(gapo_hashtag) == 1:
            gapo_hashtag = "#"+"#".join(gapo_hashtag)
        else:
            gapo_hashtag = np.nan
    gapo_hashtags.append(gapo_hashtag)
    



  3%|▎         | 996/35834 [00:00<00:06, 5209.12it/s]

['nu-tu']
['viet-nam']
['nu-tu']
['nu-tu']
['y-te']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nam-thanh']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['cuoc-song']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nam-thanh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
[]
['nu-tu']
['tinh-yeu-hen-ho']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['cuoc-song']
['anh-che-hai-huoc']
['nam-thanh', 'tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nam-thanh']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho']
[

  6%|▋         | 2300/35834 [00:00<00:05, 6140.19it/s]


['nu-tu']
['nam-thanh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['cuoc-song']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['cuoc-song']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['viet-nam']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['viet-nam']
['viet-nam']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu', 'tha-thinh']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
[]
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho', 'nu-tu']
['tinh-yeu-hen-ho']
[]
[]
['nu-tu', 'tinh-yeu-hen-ho']
['nu-tu', 'cuoc-song']
['nu-tu', 'tha-thinh']
['nu-tu', 'tha-thinh']
['nu-tu']
['han-quoc']
['lam-quen-ket-ban']
['check-in']
[]
['nu-tu']
['nu-tu', 'tha-thinh']
['tha-thinh', 'lam-quen-ket-ban']

 10%|█         | 3596/35834 [00:00<00:05, 6294.47it/s]

...


['cuoc-song']
['anh-che-hai-huoc']
['review-an-uong', 'checkin']
['nu-tu']
['nu-tu']
['bien']
['nu-tu']
['cuoc-song']
['dia-danh-du-lich']
['dia-danh-du-lich']
['nu-tu', 'tha-thinh']
['dia-danh-du-lich']
['viet-nam', 'viet-nam']
['nu-tu']
['review-an-uong']
['cuoc-song']
['cuoc-song']
['viet-nam', 'dinh-duong']
['nam-thanh']
['nam-thanh', 'lam-quen-ket-ban']
['nam-thanh']
['nu-tu']
['cuoc-song']
['nam-thanh']
['cuoc-song']
['nu-tu']
[]
['viet-nam']
[]
[]
['dinh-duong', 'do-uong']
['nu-tu']
['nu-tu']
['nu-tu']
['lam-quen-ket-ban']
['nu-tu']
['nu-tu']
['nu-tu']
['dinh-duong']
['cuoc-song']
['phong-canh']
['nu-tu']
['meo']
[]
['viet-nam']
['nu-tu']
['tinh-yeu-hen-ho']
['viet-nam', 'viet-nam']
['nu-tu']
[]
[]
['nu-tu']
['nu-tu']
['tha-thinh']
['viet-nam']
[]
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho']
['nu-tu']
['tinh-yeu-hen-ho']
['nu-tu']
['nu-tu']
['cuoc-song']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['cuoc-song']
['bong-da']
['nu-tu']
['lam-quen-ket-ban']
['nam-thanh']

100%|█████████▉| 35660/35834 [00:06<00:00, 5361.31it/s]


[]
[]
['tinh-yeu-hen-ho']
['tinh-yeu-hen-ho']
['tinh-yeu-hen-ho']
[]
['anh-che-hai-huoc']
['cuoc-song']
[]
['tinh-yeu-hen-ho']
['cuoc-song']
[]
['cuoc-song', 'nam-thanh']
['anh-che-hai-huoc']
['tinh-yeu-hen-ho']
['viet-nam', 'tinh-yeu-hen-ho']
['cuoc-song']
['cuoc-song']
['tinh-yeu-hen-ho']
['tinh-yeu-hen-ho']
['thoi-su']
['anh-che-hai-huoc']
['bong-da']
['viet-nam']
[]
['viet-nam']
['bong-da']
['viet-nam']
['cuoc-song']
['bong-da']
[]
['tinh-yeu-hen-ho']
['anh-che-hai-huoc']
['cuoc-song']
['han-quoc']
['han-quoc']
['cuoc-song']
['bong-da']
['cuoc-song']
['cuoc-song']
['bong-da']
['thoi-su']
['y-te']
['viet-nam']
['bong-da']
['bong-da']
['thoi-su', 'y-te']
['y-te']
['thoi-su']
['bong-da']
['anh-che-hai-huoc']
[]
['bien']
['y-te']
['cuoc-song']
['bong-da']
['cuoc-song']
['tinh-yeu-hen-ho']
['nu-tu']
['tinh-yeu-hen-ho']
['anh-che-hai-huoc']
['tinh-yeu-hen-ho']
['bong-da']
['bong-da']
['anh-che-hai-huoc']
['bong-da']
['tinh-yeu-hen-ho']
['tinh-yeu-hen-ho']
['bien']
['tinh-yeu-hen-ho']
['

100%|██████████| 35834/35834 [00:06<00:00, 5828.80it/s]

['bien']
['anh-che-hai-huoc']
['tinh-yeu-hen-ho']
['bien']
['bien']
['review-an-uong']
['cuoc-song']
['cuoc-song']
['cuoc-song']
[]
['review-an-uong']
[]
[]
[]
[]
[]
['nam-thanh']
['y-te']
['thoi-su']
['thoi-su']
['thoi-su']
['thoi-su']
['tinh-yeu-hen-ho']
['cuoc-song']
['nu-tu']
['dinh-duong']
['bong-da']
['cuoc-song']
['review-an-uong']
[]
[]
['cuoc-song']
[]
['tinh-yeu-hen-ho']
[]
['anh-che-hai-huoc']
['nu-tu']
['cuoc-song']
['nam-thanh']
[]
['nu-tu']
[]
['bong-da']
['nu-tu']
[]
['nu-tu']
['nam-thanh']
['nu-tu']
['tinh-yeu-hen-ho']
['tinh-yeu-hen-ho']
['nu-tu']
['tha-thinh']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho']
[]
['nu-tu']
['nu-tu']
['han-quoc']
[]
['nam-thanh']
['viet-nam']
['nu-tu']
['cuoc-song']
[]
['nam-thanh']
['nu-tu']
['cuoc-song']
['cuoc-song', 'tinh-yeu-hen-ho']
['cuoc-song', 'tinh-yeu-hen-ho']
['cuoc-song']
['cuoc-song']
['nu-tu']
['nu-tu']
['nu-tu']
['bong-da']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['nu-tu']
['tinh-yeu-hen-ho']
[]
['nu-

In [11]:
df_gapo_cleaned_not_dup.insert(loc=4, column='top_gapo_hashtag', value=gapo_hashtags)
df_gapo_cleaned_not_dup.drop('gapo_hashtag', axis = 1, inplace = True)
df_gapo_cleaned_not_dup = df_gapo_cleaned_not_dup.rename(columns={"top_gapo_hashtag": "gapo_hashtag"})
df_gapo_rule_not_nan = get_data_not_null_of_column(df=df_gapo_cleaned_not_dup,column='gapo_hashtag')
df_gapo_rule_not_nan = df_gapo_rule_not_nan.reset_index(drop=True)
df_gapo_rule_not_nan

/home/phuongdx/anaconda3/lib/python3.8/site-packages/pandas/core/frame.py:4308: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


post_id                              image_id  \
0      qqvtcmhsghi6  1a7e6c95-1f91-41e8-9d5b-269b0dbce86f   
1      qqvteeqzjgvf  58ac3938-d32e-4fe9-9e29-4a3a71e0e89a   
2      qqvto67xm19w  6b579079-271e-47c2-b662-0d40a1f42c5c   
3        qqvtp35pky  57866b3b-2a7d-4ae1-90e1-40185654140d   
4      qqvtschxj76i  30f5def9-67ee-48ef-98ba-64a10d8f120b   
...             ...                                   ...   
16176  qsz14t8onu6d  e2b5b766-fc7a-4a4c-9f1d-6b9da8c6531b   
16177  qsz15opl8fxa  8d130e93-f422-4547-ad5e-fad268e3d8f6   
16178  qsz1dv8d9829  9df4d72c-5b07-4bd3-9581-7a0e1a87e3ac   
16179  qsz3g8fzqoi0  ac10bbc1-bb00-4f5c-affd-1056be09307a   
16180  qsz3s29hmhho  80392537-e5db-4a2b-948d-83dffa23bba5   

                                                 content  \
0                                                    NaN   
1      "Từng yêu nhau, từng là của nhau thật lâu\nĐến...   
2      📣THÊM 14 CA MẮC MỚI COVID-19 NHẬP CẢNH ĐÃ ĐƯỢC...   
3                   Chẳng biết cưa chàng bắt đầu từ đâu!   
4      Thả thính sáng giờ mà hổng dính anh nào hết 💖💖...   
...                                                  ...   
16176  Tôi hỏi cái quạt là thứ tình yêu chân thành kh...   
16177  - Sao em không yêu ai?\n\n- Vì em thích cuộc s...   
16178  Phụ nữ nên có vài quy tắc😅\nĐồ của mình, mình ...   
16179                                            hali ❤💋   
16180  mì tôm mà chả có tôm\niu anh mà chả được ôm tí...   

                                               image_src  \
0      https://gapo-image.statics.pancake.vn/images/1...   
1      https://gapo-image.statics.pancake.vn/images/5...   
2      https://gapo-image.statics.pancake.vn/images/6...   
3      https://gapo-image.statics.pancake.vn/images/5...   
4      https://gapo-image.statics.pancake.vn/images/3...   
...                                                  ...   
16176  https://gapo-image.statics.pancake.vn/images/e...   
16177  https://gapo-image.statics.pancake.vn/images/8...   
16178  https://gapo-image.statics.pancake.vn/images/9...   
16179  https://gapo-image.statics.pancake.vn/images/a...   
16180  https://gapo-image.statics.pancake.vn/images/8...   

                            gapo_hashtag  
0                                 #nu-tu  
1                                 #nu-tu  
2                                  #y-te  
3                                 #nu-tu  
4                       #nu-tu#tha-thinh  
...                                  ...  
16176                             #nu-tu  
16177         #cuoc-song#tinh-yeu-hen-ho  
16178         #tinh-yeu-hen-ho#cuoc-song  
16179            #nu-tu#lam-quen-ket-ban  
16180  #nu-tu#lam-quen-ket-ban#tha-thinh  

[16181 rows x 5 columns]

In [226]:
def training_testing_splitter(input_reformat_path,train_path,valid_path):
    with open(input_path, 'r') as f:
        data_raw = csv.reader(f, delimiter=',', quoting=csv.QUOTE_ALL)
        next(data_raw)
        lable_dict = {}
        index_dict = {}
        for row in data_raw:
            label = row[5].split('#')[1::]
            try:
                lable_dict[label[0]] += 1
                index_dict[label[0]].append(row[0])
            except:
                lable_dict[label[0]] = 1
                index_dict[label[0]] = [row[0]]
    test_index = []
#  
    for key in lable_dict.keys():
        num_sample = int((lable_dict[key]*15)/100)
        test_index += random.sample(index_dict[key], num_sample)
        
    label_sorted = {k: v for k, v in sorted(lable_dict.items(), key=lambda item: item[1])}
#    
    count_0 = 0
    count_1 = 0
    with open(input_path, 'r') as f:
        data_raw = csv.reader(f, delimiter=',', quoting=csv.QUOTE_ALL)
        next(data_raw)
        with open(valid_path, 'w') as g:
            csv_writer = csv.writer(g, delimiter=',', quoting=csv.QUOTE_ALL)
            csv_writer.writerow(('', 'post_id', 'image_id', 'content', 'image_src', 'gapo_hashtag'))
            with open(train_path, 'w') as k:
                csv_writer_1 = csv.writer(k, delimiter=',', quoting=csv.QUOTE_ALL)
                csv_writer_1.writerow(('', 'post_id', 'image_id', 'content', 'image_src', 'gapo_hashtag'))
                for row in data_raw:

                    if row[0] in test_index:
                        csv_writer.writerow((count_0, row[1], row[2], row[3], row[4], row[5]))
                        count_0 += 1
                    else:
                        csv_writer_1.writerow((count_1, row[1], row[2], row[3], row[4], row[5]))
                        count_1 += 1
    

In [227]:
input_path = '/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_short_not_nan.csv'

train_path = '/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_train.csv'
valid_path = '/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_valid.csv'

train_real = '/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_standard_train.csv'
valid_real = '/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_standard_valid.csv' 



training_testing_splitter(input_path,train_path,valid_path)

In [228]:
def extract_labels(row):
#     labels = [i.strip() for i in row['gapo_hashtag'].split('#')[1:] if i.strip() in list_tag]
    labels = [i.strip() for i in row['gapo_hashtag'].split('#')[1:]]
    return labels

In [229]:
def standard_data_1(input_file, output_file):
    data = pd.read_csv(input_file)
    data['labels'] = data.apply(lambda row: extract_labels(row), axis=1)
    data = data[data.labels.str.len() != 0]
    data = data[['image_id', 'content', 'labels', 'post_id']]
    data = data.rename(columns={'content': 'content_text'})
    data.to_csv(output_file,header=False,index=False)

In [230]:
standard_data_1(train_path, train_real)
standard_data_1(valid_path, valid_real)

In [231]:
def create_dataset(img_feature_path,train_1, train_2, valid_1, valid_2):
    img_feature_file = h5py.File(img_feature_path, 'r')

    with open(train_1) as f:
        data_raw = csv.reader(f, delimiter=',', quoting=csv.QUOTE_ALL)
        with open(train_2, 'w') as g:
            csv_writer = csv.writer(g, delimiter='\t', quotechar='|', quoting=csv.QUOTE_ALL)
            for row in data_raw:
                print(row[0])
                if img_feature_file.get('image_feature_data').get(row[0]):
                    hashtag = row[2][1:-1].replace("'", "")
                    csv_writer.writerow((row[0], row[1], hashtag, row[3]))

    with open(valid_1) as f:
        data_raw = csv.reader(f, delimiter=',', quoting=csv.QUOTE_ALL)
        with open(valid_2, 'w') as g:
            csv_writer = csv.writer(g, delimiter='\t', quotechar='|', quoting=csv.QUOTE_ALL)
            for row in data_raw:
                if img_feature_file.get('image_feature_data').get(row[0]):
                    hashtag = row[2][1:-1].replace("'", "")
                    csv_writer.writerow((row[0], row[1], hashtag, row[3]))


In [ ]:
img_feature_path = '/mnt/DATA/Users/NgocPT/GAPO/old_hashtag/gapo-ai-hashtag-generation_phuongdx/data/img_vgg_feature_20210504.h5'
train_real_2 = train_real.replace('train.csv','train_1.csv')
valid_real_2 = valid_real.replace('valid.csv','valid_1.csv')

create_dataset(img_feature_path,train_real, train_real_2, valid_real, valid_real_2)

In [87]:
df_train = pd.read_csv('/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_standard_train.csv')
df_valid = pd.read_csv('/home/phuongdx/python/GAPO/data/data_01-03_to_14-06_standard_valid.csv')

In [3]:
df_train

f1ff2054-b3d0-4e1e-a81e-14bcfcb98284  \
0      f6782bfb-7327-415e-bd79-d907b611df3d   
1      1a7e6c95-1f91-41e8-9d5b-269b0dbce86f   
2      6b579079-271e-47c2-b662-0d40a1f42c5c   
3      57866b3b-2a7d-4ae1-90e1-40185654140d   
4      30f5def9-67ee-48ef-98ba-64a10d8f120b   
...                                     ...   
30421  4a029e19-68e8-40a3-b68a-9b3d2340d552   
30422  765e2df5-84b0-449e-84be-7874db188094   
30423  58eca04d-6da3-4bf9-9787-c9158c38f10f   
30424  e71f1ae7-1c69-4eba-b5b1-25ef3f789dda   
30425  bd67f266-e618-430e-a8e8-57c222226358   

      Thân em như tấm lụa đào\nLụa này hơi đắt \nAnh nào mua hông 🤭\nyoutube #nhungkaka #Gaixinh   \
0      The Remix đang sản xuất mùa tiếp theo, đ...                                            
1                                                    NaN                                            
2      📣THÊM 14 CA MẮC MỚI COVID-19 NHẬP CẢNH ĐÃ ĐƯỢC...                                            
3                   Chẳng biết cưa chàng bắt đầu từ đâu!                                            
4      Thả thính sáng giờ mà hổng dính anh nào hết 💖💖...                                            
...                                                  ...                                            
30421  Virus thì em âm tính \nNhưng thích anh thì em ...                                            
30422           Có khi nào anh thương em dù chỉ 1 lần ..                                            
30423  🥛 Sữa tươi trân châu THỐT NỐT miền Tây\n\nMới ...                                            
30424  Lí do em thấy nặng đầu \nTrên đầu có tóc trong...                                            
30425  Hoa rơi hoa rụng trước thèm \nEm đây còn ế lấy...                                            

                    ['nu-tu']  qqv8vwce7dx1  
0                ['viet-nam']  qqvr0i7zhqk3  
1                   ['nu-tu']  qqvtcmhsghi6  
2                    ['y-te']  qqvto67xm19w  
3                   ['nu-tu']    qqvtp35pky  
4      ['nu-tu', 'tha-thinh']  qqvtschxj76i  
...                       ...           ...  
30421               ['nu-tu']  quoqzjhp0c61  
30422               ['nu-tu']  quor11sk0bl1  
30423      ['review-an-uong']  quor63x31fy9  
30424               ['nu-tu']  quor6ehr16kb  
30425               ['nu-tu']  quor7mg4wbiz  

[30426 rows x 4 columns]

In [88]:
df_train.columns = ['image_id', 'content', 'label', 'post_id']
df_valid.columns = ['image_id', 'content', 'label', 'post_id']

In [96]:
labels_train = []
label = df_train['label']
labels_valid = []
labelv = df_valid['label']

In [97]:
# for index, row in df_train.iterrows():
#     label = row[2][1:][:-1]
#     a =list(label.split(', '))
#     labels_train += a
# print(labels_train)

for index, row in df_valid.iterrows():
    labelv = row[2][1:][:-1]
    a =list(labelv.split(', '))
    labels_valid += a
print(labels_valid)

["'nu-tu'", "'tha-thinh'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nam-thanh'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'tinh-yeu-hen-ho'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'cuoc-song'", "'tinh-yeu-hen-ho'", "'ban-hang_ban-hang'", "'dien-thoai'", "'ban-hang_ban-hang'", "'do-choi-cong-nghe'", "'cong-thuc-nau-an-pha-che'", "'checkin'", "'ban-hang_ban-hang'", "'ban-hang_ban-hang'", "'tinh-yeu-hen-ho'", "'nu-tu'", "'choi-ga'", "'ga'", "'cuoc-song'", "'nu-tu'", "'nu-tu'", "'chup-anh-nghe-thuat'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'tinh-yeu-hen-ho'", "'anh-che-hai-huoc'", "'gia-dinh_tre-con'", "'meo'", "'makeup-skin-care'", "'lam-quen-ket-ban'", "'nu-tu'", "'nu-tu'", "'anh-che-hai-huoc'", "'chau-a'", "'nu-tu'", "'anh-che-hai-huoc'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'nu-tu'", "'khac'", "'bong-da'", "'bong-da'", "'tinh-yeu-hen-ho'", "'thoi-su'", "'y-te'", "'tennis'", "'review-an-uong'", "'phap-luat'", "'bong-da'", "'review-an-uong'", "'bong-da'", "'tinh-yeu-h

In [98]:
from collections import Counter
# print(Counter(labels_train))
print(Counter(labels_valid))

Counter({"'nu-tu'": 2135, "'tinh-yeu-hen-ho'": 444, "'cuoc-song'": 388, "'anh-che-hai-huoc'": 293, "'nam-thanh'": 279, "'lam-quen-ket-ban'": 271, "'bong-da'": 187, "'thoi-su'": 166, "'viet-nam'": 156, "'bien'": 141, "'dia-danh-du-lich'": 129, "'review-an-uong'": 116, "'y-te'": 104, "'tha-thinh'": 84, "'o-to'": 80, "'han-quoc'": 55, "'cong-thuc-nau-an-pha-che'": 52, "'ban-hang_ban-hang'": 44, "'meo'": 41, "'chup-anh-nghe-thuat'": 38, "'xe-may'": 34, "'gia-dinh_tre-con'": 32, "'us-uk'": 32, "'kien-thuc'": 31, "'khoa-hoc-cong-nghe'": 31, "'dien-thoai'": 30, "'checkin'": 30, "'giai-tri'": 29, "'cho'": 29, "'check-in'": 25, "'truyen-cam-hung'": 22, "'tennis'": 19, "'cong-viec'": 18, "'chau-a'": 17, "'lich-su'": 16, "'ga'": 15, "'meme'": 15, "'dinh-duong'": 15, "'chia-se-kinh-nghiem'": 15, "'phong-canh'": 15, "'hoi-hoa'": 13, "'tho'": 13, "'khac'": 12, "'giao-thong'": 11, "'sach'": 11, "'ban-be'": 11, "'the-gioi'": 9, "'game-chien-thuat-lol-dota-'": 9, "'tam-ly-tinh-cam'": 9, "'cham-soc'": 9

In [95]:
# d = Counter(labels_train)
# df = pd.DataFrame.from_dict(d, orient='index').reset_index()
# df = df.rename(columns={'index':'label', 0:'count'})
# df.to_csv('/home/phuongdx/python/GAPO/data/count_labels_train.csv')
d = Counter(labels_valid)
df = pd.DataFrame.from_dict(d, orient='index').reset_index()
df = df.rename(columns={'index':'label', 0:'count'})
df.to_csv('/home/phuongdx/python/GAPO/data/count_labels_valid.csv')
df

label  count
0         'viet-nam'    926
1            'nu-tu'  12110
2             'y-te'    627
3        'tha-thinh'    424
4        'nam-thanh'   1576
..               ...    ...
95       'game-show'     22
96             'rap'     12
97         'do-uong'     44
98  'video-hai-huoc'     10
99        'noi-that'     11

[100 rows x 2 columns]